# Assignment 2: IR

## Preparations
* Put all your imports, and path constants in the next cells
* Make sure all your path constants are **relative to** ***DATA_DIR*** and **NOT hard-coded** in your code.

In [136]:
!pip install whoosh
!pip install pytrec_eval
!pip install wget
!pip install sklearn
!pip install numpy

In [137]:
import wget
wget.download("https://github.com/MIE451-1513-2019/course-datasets/raw/master/government.zip", "government.zip")

'government (9).zip'

In [138]:
!unzip government.zip

Archive:  government.zip
replace government/topics-with-full-descriptions.txt? [y]es, [n]o, [A]ll, [N]one, [r]ename: A
  inflating: government/topics-with-full-descriptions.txt  
  inflating: government/gov.topics   
  inflating: government/gov.qrels    
  inflating: government/documents/61/G00-61-2800209  
  inflating: government/documents/61/G00-61-1192048  
  inflating: government/documents/61/G00-61-1118212  
  inflating: government/documents/61/G00-61-0749882  
  inflating: government/documents/61/G00-61-2230501  
  inflating: government/documents/61/G00-61-0680698  
  inflating: government/documents/61/G00-61-0551387  
  inflating: government/documents/61/G00-61-2575433  
  inflating: government/documents/61/G00-61-0469713  
  inflating: government/documents/61/G00-61-0280746  
  inflating: government/documents/61/G00-61-2574316  
  inflating: government/documents/61/G00-61-3933997  
  inflating: government/documents/61/G00-61-3290635  
  inflating: government/documents/61/G00-61

In [0]:
# imports
# Put all your imports here
import wget
from whoosh import index, writing
from whoosh.fields import Schema, TEXT, KEYWORD, ID, STORED
from whoosh import qparser
from whoosh.analysis import *
from whoosh.qparser import QueryParser
from whoosh import scoring
import os.path
from pathlib import Path
import tempfile
import subprocess
import pytrec_eval
import nltk
from nltk.stem import *
from nltk.corpus import stopwords
from whoosh.analysis import Filter
from sklearn.model_selection import ParameterGrid
import numpy

In [0]:
DATA_DIR = "government"
#
# Put other path constants here
#
DOCUMENTS_DIR = os.path.join(DATA_DIR, "documents")
TOPIC_FILE = os.path.join(DATA_DIR, "gov.topics")
QRELS_FILE = os.path.join(DATA_DIR, "gov.qrels")

## Question 1
Provide your text answers in the following two markdown cells

### Q1 (a): Provide answer to Q1 (a) here [markdown cell]
**Answer Q1 (a):** <br>Rprec

### Q1 (b): Provide answer to Q1 (b) here [markdown cell]
**Answer Q1 (b):** <br>
Rprec measures the precent of relevant results out of top R-(num_rel for a query) which is appropriate for goverment website wherein objective is to minimize the time user spends looking for information by showing relevant results at the top.

---



## Question 2


### Q2 (a): Write your code below

In [0]:
# Put your code for creating the index here (you can add more cells).
# Make sure you save the final index in the variable INDEX_Q2, your query parser in QP_Q2, and your searcher in SEARCHER_Q2
def createIndex(schema):
    # Generate a temporary directory for the index
    indexDir = tempfile.mkdtemp()

    # create and return the index
    return index.create_in(indexDir, schema)

def addFilesToIndex(indexObj, fileList):
    # open writer
    writer = writing.BufferedWriter(indexObj, period=None, limit=1000)

    try:
        # write each file to index
        for docNum, filePath in enumerate(fileList):
            with open(filePath, "r", encoding="utf-8") as f:
                fileContent = f.read()
                writer.add_document(file_path = filePath,
                                    file_content = fileContent)

                # print status every 1000 documents
                if (docNum+1 % 1000 == 0):
                    print("already indexed:", docNum+1)
        print("done indexing.")

    finally:
        # close the index
        writer.close()  

In [0]:
# Build a list of files to index
filesToIndex = [str(filePath) for filePath in Path(DOCUMENTS_DIR).glob("**/*") if filePath.is_file()]

In [143]:
# Check the list
filesToIndex[:5]

['government/documents/80/G00-80-1408326',
 'government/documents/80/G00-80-1361789',
 'government/documents/80/G00-80-2913262',
 'government/documents/80/G00-80-1849469',
 'government/documents/80/G00-80-0939068']

In [144]:
# count files to index
print("number of files:", len(filesToIndex))

number of files: 4078


In [0]:
# first, define a Schema for the index
SCHEMA_Q2 = Schema(file_path = ID(stored=True),
                  file_content = TEXT(analyzer = RegexTokenizer()))
# now, create the index at the path INDEX_DIR based on the new schema
myIndex = createIndex(SCHEMA_Q2) 

In [0]:
INDEX_Q2=myIndex # Replace None with your index for Q2

In [147]:
addFilesToIndex(INDEX_Q2, filesToIndex)

done indexing.


In [0]:
# define a query parser for the field "file_content" in the index
QP_Q2 = QueryParser("file_content", schema=INDEX_Q2.schema) # Replace None with your query parser for Q2
SEARCHER_Q2 = INDEX_Q2.searcher() # Replace None with your searcher for Q2

In [0]:
def pyTrecEval(topicFile, qrelsFile, queryParser, searcher):
    # Load topic file - a list of topics(search phrases) used for evalutation
    with open(topicFile, "r") as tf:
        topics = tf.read().splitlines()

    # create an output file to which we'll write our results
    tempOutputFile = tempfile.mkstemp()[1]
    with open(tempOutputFile, "w") as outputTRECFile:
        # for each evaluated topic:
        # build a query and record the results in the file in TREC_EVAL format
        for topic in topics:
            topic_id, topic_phrase = tuple(topic.split(" ", 1))
            print(topic_id, topic_phrase)
            topicQuery = queryParser.parse(topic_phrase)
            topicResults = searcher.search(topicQuery, limit=None)
            for (docnum, result) in enumerate(topicResults):
                score = topicResults.score(docnum)
                print("%s Q0 %s %d %lf test\n" % (topic_id, os.path.basename(result["file_path"]), docnum, score))
                outputTRECFile.write("%s Q0 %s %d %lf test\n" % (topic_id, os.path.basename(result["file_path"]), docnum, score))
    with open(qrelsFile, 'r') as f_qrel:
        qrel = pytrec_eval.parse_qrel(f_qrel)

    with open(tempOutputFile, 'r') as f_run:
        run = pytrec_eval.parse_run(f_run)

    evaluator = pytrec_eval.RelevanceEvaluator(
        qrel, pytrec_eval.supported_measures)

    results = evaluator.evaluate(run)
    def print_line(measure, scope, value):
        print('{:25s}{:8s}{:.4f}'.format(measure, scope, value))
    for query_id, query_measures in results.items():
        for measure, value in query_measures.items():
            if measure == "runid":
              continue
            print_line(measure, query_id, value)
    for measure in query_measures.keys():
        if measure == "runid":
              continue
        print_line(
            measure,
            'all',
            pytrec_eval.compute_aggregated_measure(
                measure,
                [query_measures[measure]
                 for query_measures in results.values()]))

In [150]:
pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q2, SEARCHER_Q2)

1 mining gold silver coal
1 Q0 G00-90-0342721 0 26.645398 test

2 juvenile delinquency
2 Q0 G00-22-3396139 0 17.262139 test

2 Q0 G00-76-0415824 1 10.597055 test

2 Q0 G00-78-1531079 2 8.778648 test

2 Q0 G00-15-1718631 3 8.076860 test

2 Q0 G00-70-2787853 4 6.788751 test

2 Q0 G00-74-1394517 5 3.368380 test

4 wireless communications
4 Q0 G00-99-2247765 0 16.449155 test

4 Q0 G00-85-1525415 1 13.364613 test

4 Q0 G00-05-1218739 2 12.956314 test

4 Q0 G00-09-0774298 3 11.781349 test

4 Q0 G00-56-4151981 4 11.367248 test

4 Q0 G00-21-2229498 5 10.743958 test

4 Q0 G00-98-4068688 6 10.464865 test

4 Q0 G00-47-2117970 7 10.213356 test

4 Q0 G00-67-0152545 8 8.392871 test

4 Q0 G00-06-1757034 9 6.431556 test

4 Q0 G00-78-2551063 10 3.955775 test

4 Q0 G00-84-0274223 11 2.068438 test

6 physical therapists
6 Q0 G00-26-3134051 0 13.996502 test

6 Q0 G00-59-0786269 1 13.853934 test

6 Q0 G00-60-3914816 2 11.345260 test

6 Q0 G00-21-0649032 3 5.955903 test

6 Q0 G00-45-4032177 4 5.937137 test


In [0]:
def printRelName(topicFile, qrelsFile, queryParser, searcher, id):
  with open(topicFile, "r") as tf:
        topics = tf.read().splitlines()
  for topic in topics:
        topic_id, topic_phrase = tuple(topic.split(" ", 1))
        if topic_id == id:
          print("---------------------------Topic_id and Topic_phrase----------------------------------")
          print(topic_id, topic_phrase)
          topicQuery = queryParser.parse(topic_phrase)
          topicResults = searcher.search(topicQuery, limit=None)
          print("---------------------------Return documents----------------------------------")
          for (docnum, result) in enumerate(topicResults):
              score = topicResults.score(docnum)
              print("%s Q0 %s %d %lf test" % (topic_id, os.path.basename(result["file_path"]), docnum, score))
          print("---------------------------Relevant documents----------------------------------")
          with open(qrelsFile, 'r') as f_qrel:
            qrels = f_qrel.readlines()
            for i in qrels:
              qid, _, doc, rel = i.rstrip().split(" ")
              if qid == id and rel == "1":
                print(i.rstrip())

In [152]:
printRelName(TOPIC_FILE, QRELS_FILE, QP_Q2, SEARCHER_Q2, "2")

---------------------------Topic_id and Topic_phrase----------------------------------
2 juvenile delinquency
---------------------------Return documents----------------------------------
2 Q0 G00-22-3396139 0 17.262139 test
2 Q0 G00-76-0415824 1 10.597055 test
2 Q0 G00-78-1531079 2 8.778648 test
2 Q0 G00-15-1718631 3 8.076860 test
2 Q0 G00-70-2787853 4 6.788751 test
2 Q0 G00-74-1394517 5 3.368380 test
---------------------------Relevant documents----------------------------------
2 0 G00-08-1145623 1
2 0 G00-37-1427392 1


In [153]:
# define a reader object on the index
Reader_Q2 = INDEX_Q2.reader()
#how many terms do we have?
print("# terms in Q2:",Reader_Q2.field_length("file_content"))
# how many documents have the phares "juvenile", delinquency"
#   in the field "file_content"?
print("# docs with 'juvenile' in Q2:", Reader_Q2.doc_frequency("file_content", "juvenile"))
print("# docs with 'delinquency' in Q2:", Reader_Q2.doc_frequency("file_content", "delinquency"))


# how many phares "juvenile", "delinquency"
#   in the field "file_content"?
print("# with 'juvenile' in Q2:", Reader_Q2.frequency("file_content", "juvenile"))
print("# with 'delinquency' in Q2:", Reader_Q2.frequency("file_content", "delinquency"))

# terms in Q2: 2165181
# docs with 'juvenile' in Q2: 19
# docs with 'delinquency' in Q2: 6
# with 'juvenile' in Q2: 65.0
# with 'delinquency' in Q2: 8.0


In [154]:
print("most distinctive terms in Q2 are:", Reader_Q2.most_distinctive_terms("file_content", number=6))

most distinctive terms in Q2 are: [(15793.691041995347, b'the'), (12141.916574922074, b'and'), (11322.7204750335, b'in'), (11181.871195315607, b'of'), (10654.852924162624, b'a'), (9400.984123915898, b'Gamma')]


### Q2 (b): Provide answer to Q2 (b) here [markdown cell]
**Answer Q2 (b):** <br>Rprec= 0.1667

### Q2 (c): Provide answer to Q2(c) here [markdown cell]
**Answer Q2 (c):**<br>**Good performance for Topic IDs:** 18 and 24 <br>
**Bad performance for Topic IDs:** 1,2,6,7,9,16,19,28

## Question 3

### Q3 (a): Provide answer to Q3 (a) here [markdown cell]
**Answer Q3 (a):**<br> 
<b>Chosen Query/ Topic: </b> 2 juvenile delinquency <br>
<p><b>Reason for Choosing Topics ID-2: </b><br>This query has false positives (Irrelevant documents retrieved or irrelevant documents ranked highly), false negative (Relevant documents not retrieved or relevant documents not ranked highly). Moreover, this topic ID was improved partially with further scope of improvement from baseline (Q2) to Q3 <br>
<p><b>Documents highly ranked:</b> (obtained using function printRelName())

1. G00-22-3396139 (False Positive with respect to Q2)
2. G00-76-0415824 (False Positive with respect to Q2)
3. G00-78-1531079 (False Positive with respect to Q2)
4. G00-15-1718631 (False Positive with respect to Q2)
5. G00-70-2787853 (False Positive with respect to Q2)
6. G00-74-1394517 (False Positive with respect to Q2)

<b>Documents that should have been highly ranked:</b> (obtained using function printRelName())
1. G00-08-1145623 (False Negative with respect to Q2)
2. G00-37-1427392 (False Negative with respect to Q2)

<b>False Negative Analysis:</b> Chosen Document- G00-37-1427392 <br>
Tokens obtained from the INDEX_Q2: ['juvenile', 'delinquency'] <br>
<p>Since the analyzer only consists of RegexTokenizer(), the query being matched with the documents is case sensitive. For instance, since the query after parsing through the analyzer is ['juvenile', 'delinquency'] doucments with the term 'Juvenile' and 'Delinquency' is not accounted here. <br>
<p>Consequently, the term frequency of "juvenile" and "delinquency" for the document-G00-37-1427392  was 3 and 0 respectively. However, the actual frequency should have been 9 and 5 for "juvenile" and "delinquency" respectively.
<p>Importantly, by default, the parser treats the words as if they were connected by AND, meaning all the terms must be present for a document to match [https://whoosh.readthedocs.io/en/latest/parsing.html]
  
<p>Thus, for this query, Document G00-37-1427392 is not retrieved since as per the analyzer, <b>"juvenile" is present in this document but not "delinquency"</b>     
  
<b>False Positive Analysis:</b> Chosen Document- G00-22-3396139 <br>
On the similar grounds as discussed above, the term frequency of "juvenile" and "delinquency" for the document-G00-22-3396139  was 1 and 1 respectively. Since <b>both "juvenile" and "delinquency"</b> is obtained for this document, it is retrieved and ranked highly relative to the other retieved documents.
  
<b>Results obtained from Inspecting Index:</b>
<br># terms in Q2:  2165181
<br># docs with 'juvenile' in Q2:  19
<br># docs with 'delinquency' in Q2:  6
<br># 'juvenile' in Q2:  65.0
<br># 'delinquency' in Q2:  8.0
<br>Most Distinctive Terms: Terms with the highest tf*idf scores obtained are the stopwords [(15793.691041995347, b'the'),
 (12141.916574922074, b'and'),
 (11322.7204750335, b'in'),
 (11181.871195315607, b'of'),
 (10654.852924162624, b'a'),
 (9400.984123915898, b'Gamma')]
  

<b>Suggested Modifications:</b><br>
 1. Configuring the QueryParser using the group keyword argument-qparser.OrGroup<br>
  <b>Motivation:</b> Documents containing "juvenile" OR "delinquency" will be matched and retrieved. Thus, this will aid in retrieving the document-G00-37-1427392.
 2. Using LowercaseFilter() in the analyzer<br>
  <b>Motivation:</b> This will covert the query as well as the terms in the documents to lowercase making the search case-insentive.
 3. Using StopFilter() in the analyer<br>
  <b>Motivation:</b> Filtering the stopwords will aid in giving higher weightage to the rare terms occuring frequently in a document.

### Q3 (b): Write your code below

In [155]:
# Put your code for creating the index here (you can add more cells).
LwrStpAnalyzer = RegexTokenizer() | LowercaseFilter() | StopFilter()
# define a Schema with the new analyzer
SCHEMA_Q3 = Schema(file_path = ID(stored=True),
                   file_content = TEXT(analyzer = LwrStpAnalyzer))

# create the index based on the new schema
INDEX_Q3 = createIndex(SCHEMA_Q3)
addFilesToIndex(INDEX_Q3, filesToIndex)
# Make sure you save the final index in the variable INDEX_Q3, your query parser in QP_Q3, and your searcher in SEARCHER_Q3

done indexing.


In [0]:
# INDEX_Q3 = None # Replace None with your index for Q3
QP_Q3 = QueryParser("file_content", schema=INDEX_Q3.schema,group=qparser.OrGroup) # Replace None with your query parser for Q3
SEARCHER_Q3 = INDEX_Q3.searcher() # Replace None with your searcher for Q3

In [157]:
pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q3, SEARCHER_Q3)

1 mining gold silver coal
1 Q0 G00-07-1172041 0 23.797650 test

1 Q0 G00-86-3214229 1 23.280154 test

1 Q0 G00-90-0342721 2 22.803461 test

1 Q0 G00-21-2004003 3 22.618556 test

1 Q0 G00-42-1455285 4 21.533205 test

1 Q0 G00-27-2048511 5 20.408459 test

1 Q0 G00-23-3149835 6 20.098413 test

1 Q0 G00-34-1044519 7 19.285438 test

1 Q0 G00-32-2907392 8 19.215345 test

1 Q0 G00-50-2059900 9 19.213512 test

1 Q0 G00-94-0326199 10 19.157402 test

1 Q0 G00-26-0088644 11 19.129445 test

1 Q0 G00-24-4085400 12 19.045416 test

1 Q0 G00-02-0351712 13 18.981322 test

1 Q0 G00-74-1802348 14 18.401440 test

1 Q0 G00-31-1216640 15 18.303411 test

1 Q0 G00-10-3730888 16 17.118876 test

1 Q0 G00-01-2689026 17 17.027944 test

1 Q0 G00-98-3517069 18 16.816891 test

1 Q0 G00-48-3798484 19 16.727984 test

1 Q0 G00-62-3289850 20 16.165935 test

1 Q0 G00-27-2669897 21 15.978823 test

1 Q0 G00-91-0853670 22 15.407921 test

1 Q0 G00-08-0995170 23 15.251655 test

1 Q0 G00-73-3632837 24 15.135145 test

1 Q0 G00-

In [158]:
printRelName(TOPIC_FILE, QRELS_FILE, QP_Q3, SEARCHER_Q3, "2")

---------------------------Topic_id and Topic_phrase----------------------------------
2 juvenile delinquency
---------------------------Return documents----------------------------------
2 Q0 G00-37-1427392 0 19.090128 test
2 Q0 G00-22-3396139 1 19.085040 test
2 Q0 G00-78-1531079 2 16.820244 test
2 Q0 G00-92-0578141 3 16.051704 test
2 Q0 G00-67-0637954 4 15.360254 test
2 Q0 G00-91-1567424 5 15.360254 test
2 Q0 G00-94-1117794 6 13.872165 test
2 Q0 G00-76-0415824 7 12.874618 test
2 Q0 G00-15-1718631 8 11.736098 test
2 Q0 G00-90-3871013 9 11.715659 test
2 Q0 G00-54-0037064 10 10.939045 test
2 Q0 G00-24-0028328 11 10.607220 test
2 Q0 G00-48-2351509 12 10.235109 test
2 Q0 G00-00-1902126 13 10.117290 test
2 Q0 G00-93-1635202 14 10.011797 test
2 Q0 G00-54-3411561 15 9.909443 test
2 Q0 G00-95-0708680 16 9.414607 test
2 Q0 G00-17-1852046 17 9.229138 test
2 Q0 G00-70-2787853 18 9.116448 test
2 Q0 G00-27-2159399 19 8.939224 test
2 Q0 G00-65-1451613 20 8.920277 test
2 Q0 G00-10-4116640 21 8.80846

In [159]:
[token.text for token in LwrStpAnalyzer("juvenile delinquency")]

['juvenile', 'delinquency']

In [160]:
# define a reader object on the index
Reader_Q3 = INDEX_Q3.reader()
#how many terms do we have?
print("Total number of terms in Q3:",Reader_Q3.field_length("file_content"))

# how many documents have the phares "juvenile", delinquency"
#   in the field "file_content"?
print("# docs with 'juvenile' in Q3:", Reader_Q3.doc_frequency("file_content", "juvenile"))
print("# docs with 'delinquency' in Q3:", Reader_Q3.doc_frequency("file_content", "delinquency"))


# how many phares "juvenile", delinquency"
#   in the field "file_content"?
print("# with 'juvenile' in Q3:", Reader_Q3.frequency("file_content", "juvenile"))
print("# with 'delinquency' in Q3:", Reader_Q3.frequency("file_content", "delinquency"))

Total number of terms in Q3: 1591655
# docs with 'juvenile' in Q3: 49
# docs with 'delinquency' in Q3: 14
# with 'juvenile' in Q3: 179.0
# with 'delinquency' in Q3: 29.0


In [161]:
# list indexed terms for field "file_content"
[term for term in Reader_Q3.field_terms("file_content")][1000:1010]

['01235',
 '0125655',
 '0128',
 '0129',
 '012a',
 '012b',
 '013',
 '013.gif',
 '0130',
 '0133']

### Q3 (c): Provide answer to Q3 (c) here [markdown cell]
**Answer Q3 (c):**<br> 
<b>Modifications Made:</b>
 1. Configuring the QueryParser using the group keyword argument-qparser.OrGroup<br>
 2. Using LowercaseFilter() in the analyzer<br>
 3. Using StopFilter() in the analyer<br>

<b>Results Analysis for Q3:</b> (With respect to the chose measure- Rprec)
 1. <b>Improved Topic IDs:</b> 2, 4, 14, 19  
 2. <b>Topic IDs with same performance:</b> 18,24
 3. <b>Worsened Topic IDs:</b> None
  
<b>Detailed Analysis of Topics ID 2:</b> juvenile delinquency<br>
Documents highly ranked: (obtained using function printRelName())

G00-37-1427392 (True Positive with respect to Q3)<br>
G00-22-3396139<br>
G00-78-1531079<br>
G00-92-0578141<br>
G00-67-0637954<br>
G00-91-1567424<br>
G00-94-1117794<br>
G00-76-0415824<br>
G00-15-1718631<br>
G00-90-3871013<br>
G00-54-0037064<br>
G00-24-0028328<br>
G00-48-2351509<br>
G00-00-1902126<br>
G00-93-1635202<br>
G00-54-3411561<br>
G00-95-0708680<br>
G00-17-1852046<br>
G00-70-2787853<br>
G00-27-2159399<br>
G00-65-1451613<br>
G00-10-4116640<br>
G00-52-2562368<br>
G00-08-1145623 (True Positive with respect to Q3)<br>
G00-00-1717907<br>
G00-37-3530053<br>
G00-11-0021900<br>
G00-95-0245120<br>
G00-11-0737967<br>
G00-74-1546702<br>
G00-01-2292288<br>
G00-11-2416074<br>
G00-29-2968932<br>
G00-56-2550885<br>
G00-78-3252910<br>
G00-46-2672308<br>
G00-30-3726817<br>
G00-79-3110767<br>
G00-79-0620805<br>
G00-88-1028808<br>
G00-08-0239407<br>
G00-63-1804150<br>
G00-15-1460278<br>
G00-74-1394517<br>
G00-30-3863788<br>
G00-65-0346398<br>
G00-86-3730053<br>
G00-56-3884873<br>
G00-33-2347653<br>
G00-24-3625720<br>

<b>Documents that should have been highly ranked:</b> (obtained using function printRelName())

G00-08-1145623 (True Positive with respect to Q3)
G00-37-1427392 (True Positive with respect to Q3)

<b>Results obtained from Inspecting Index:</b>
<br>Total number of terms in Q3: 1591655
<br># docs with 'juvenile' in Q3: 49
<br># docs with 'delinquency' in Q3: 14
<br># with 'juvenile' in Q3: 179.0
<br># with 'delinquency' in Q3: 29.0

<b>Improvements:</b> (With respect to the chose measure- Rprec)
1. Topic ID 2: From 0 in Q2 to 0.5 in Q3
2. Overall: From 0.1667 in Q2 to 0.3 in Q3   

### Q3 (d): Provide answer to Q3 (d) here [markdown cell]
**Answer Q3 (d):**<br> 
Yes

### Q3 (e): Provide answer to Q3 (e) here [markdown cell]
**Answer Q3 (e):**<br> 
No- Since some queries got better with none performing worse than Q2

### Q3 (f): Provide answer to Q3 (f) here [markdown cell]
**Answer Q3 (f):**<br> 
The idea was good for following reasons:<br>
1. Performance of 4 queries improved and none got worse
2. Overall performance improved for all the queries <br>

However, with respect to the chosen measure- Rprec, Topic IDs 1, 6, 7, 9, 10, 16, 22, 28 did not show any improvement and there is further scope of improvement for Topic IDs 2, 4 and 19. This calls for deep diving into the search engine optimization.

## Question 4

In [0]:
# Put your code for creating the index here (you can add more cells).
# Make sure you save the final index in the variable INDEX_Q4, your query parser in QP_Q4, and your searcher in SEARCHER_Q4

In [163]:
# download required resources
nltk.download("wordnet")

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [0]:
class CustomFilter(Filter):
    is_morph = True
    def __init__(self, filterFunc, *args, **kwargs):
        self.customFilter = filterFunc
        self.args = args
        self.kwargs = kwargs
    def __eq__(self):
        return (other
                and self.__class__ is other.__class__)
    def __call__(self, tokens):
        for t in tokens:
            if t.mode == 'query': # if called by query parser
                t.text = self.customFilter(t.text, *self.args, **self.kwargs)
                yield t
            else: # == 'index' if called by indexer
                t.text = self.customFilter(t.text, *self.args, **self.kwargs)
                yield t

In [165]:
# Iteration 1. Stemming- Finding Optimal Stemmer
LwrStpStmAnalyzer1 = RegexTokenizer() | LowercaseFilter() | StopFilter() | StemFilter()
# define a Schema with the new analyzer
SCHEMA_Q4_11 = Schema(file_path = ID(stored=True),
                   file_content = TEXT(analyzer = LwrStpStmAnalyzer1))

# create the index based on the new schema
INDEX_Q4_11 = createIndex(SCHEMA_Q4_11)
addFilesToIndex(INDEX_Q4_11, filesToIndex)

done indexing.


In [0]:
QP_Q4_11 = QueryParser("file_content", schema=INDEX_Q4_11.schema,group=qparser.OrGroup) # Replace None with your query parser for Q4_11
SEARCHER_Q4_11 = INDEX_Q4_11.searcher() # Replace None with your searcher for Q4_11

In [167]:
pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q4_11, SEARCHER_Q4_11)

1 mining gold silver coal
1 Q0 G00-90-0342721 0 24.425422 test

1 Q0 G00-07-1172041 1 23.863735 test

1 Q0 G00-86-3214229 2 23.413138 test

1 Q0 G00-21-2004003 3 22.437986 test

1 Q0 G00-42-1455285 4 21.772115 test

1 Q0 G00-48-3798484 5 20.531929 test

1 Q0 G00-23-3149835 6 20.071361 test

1 Q0 G00-27-2048511 7 19.870874 test

1 Q0 G00-32-2907392 8 19.389264 test

1 Q0 G00-50-2059900 9 19.213512 test

1 Q0 G00-02-0351712 10 19.165341 test

1 Q0 G00-26-0088644 11 19.129445 test

1 Q0 G00-34-1044519 12 19.113910 test

1 Q0 G00-24-4085400 13 19.033231 test

1 Q0 G00-94-0326199 14 18.773146 test

1 Q0 G00-31-1216640 15 18.701529 test

1 Q0 G00-74-1802348 16 18.632754 test

1 Q0 G00-73-3632837 17 18.216664 test

1 Q0 G00-98-3517069 18 17.852850 test

1 Q0 G00-10-3730888 19 17.771361 test

1 Q0 G00-01-2689026 20 17.236037 test

1 Q0 G00-27-2669897 21 16.951894 test

1 Q0 G00-27-3209717 22 16.502528 test

1 Q0 G00-00-1006224 23 16.399435 test

1 Q0 G00-02-1239993 24 16.170523 test

1 Q0 G00-

In [168]:
# Iteration 1. Stemming- Finding Optimal Stemmer
# Put your code for creating the index here (you can add more cells).
LwrStpStmAnalyzer2 = RegexTokenizer() | LowercaseFilter() | StopFilter() | CustomFilter(LancasterStemmer().stem)

# define a Schema with the new analyzer
SCHEMA_Q4_12 = Schema(file_path = ID(stored=True),
                   file_content = TEXT(analyzer = LwrStpStmAnalyzer2))

# create the index based on the new schema
INDEX_Q4_12 = createIndex(SCHEMA_Q4_12)
addFilesToIndex(INDEX_Q4_12, filesToIndex)

done indexing.


In [0]:
QP_Q4_12 = QueryParser("file_content", schema=INDEX_Q4_12.schema,group=qparser.OrGroup) # Replace None with your query parser for Q4_12
SEARCHER_Q4_12 = INDEX_Q4_12.searcher() # Replace None with your searcher for Q4_12

In [170]:
pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q4_12, SEARCHER_Q4_12)

1 mining gold silver coal
1 Q0 G00-90-0342721 0 21.402671 test

1 Q0 G00-07-1172041 1 20.550081 test

1 Q0 G00-86-3214229 2 20.063262 test

1 Q0 G00-21-2004003 3 19.406326 test

1 Q0 G00-48-3798484 4 18.535640 test

1 Q0 G00-42-1455285 5 18.245675 test

1 Q0 G00-26-0088644 6 18.072792 test

1 Q0 G00-50-2059900 7 17.967568 test

1 Q0 G00-23-3149835 8 17.774729 test

1 Q0 G00-27-2048511 9 17.569063 test

1 Q0 G00-32-2907392 10 17.072780 test

1 Q0 G00-73-3632837 11 16.947574 test

1 Q0 G00-31-1216640 12 16.827685 test

1 Q0 G00-02-0351712 13 16.817457 test

1 Q0 G00-34-1044519 14 16.800432 test

1 Q0 G00-94-0326199 15 16.579828 test

1 Q0 G00-74-1802348 16 16.467217 test

1 Q0 G00-24-4085400 17 16.377224 test

1 Q0 G00-98-3517069 18 15.734774 test

1 Q0 G00-10-3730888 19 15.553479 test

1 Q0 G00-01-2689026 20 15.100029 test

1 Q0 G00-27-2669897 21 14.697374 test

1 Q0 G00-27-3209717 22 14.337521 test

1 Q0 G00-08-0995170 23 14.262627 test

1 Q0 G00-00-1006224 24 14.203220 test

1 Q0 G00-

In [171]:
# Iteration 1. Stemming- Finding Optimal Stemmer
# Put your code for creating the index here (you can add more cells).
LwrStpStmAnalyzer3 = RegexTokenizer() | LowercaseFilter() | StopFilter() | CustomFilter(SnowballStemmer("english").stem)
# define a Schema with the new analyzer
SCHEMA_Q4_13 = Schema(file_path = ID(stored=True),
                   file_content = TEXT(analyzer = LwrStpStmAnalyzer3))

# create the index based on the new schema
INDEX_Q4_13 = createIndex(SCHEMA_Q4_13)
addFilesToIndex(INDEX_Q4_13, filesToIndex)

done indexing.


In [172]:
QP_Q4_13 = QueryParser("file_content", schema=INDEX_Q4_13.schema,group=qparser.OrGroup) # Replace None with your query parser for Q4_13
SEARCHER_Q4_13 = INDEX_Q4_13.searcher() # Replace None with your searcher for Q4_13

pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q4_13, SEARCHER_Q4_13)

1 mining gold silver coal
1 Q0 G00-90-0342721 0 24.425422 test

1 Q0 G00-07-1172041 1 23.863735 test

1 Q0 G00-86-3214229 2 23.413138 test

1 Q0 G00-21-2004003 3 22.437986 test

1 Q0 G00-42-1455285 4 21.772115 test

1 Q0 G00-48-3798484 5 20.531929 test

1 Q0 G00-23-3149835 6 20.071361 test

1 Q0 G00-27-2048511 7 19.870874 test

1 Q0 G00-32-2907392 8 19.389264 test

1 Q0 G00-50-2059900 9 19.213512 test

1 Q0 G00-02-0351712 10 19.165341 test

1 Q0 G00-26-0088644 11 19.129445 test

1 Q0 G00-34-1044519 12 19.113910 test

1 Q0 G00-24-4085400 13 19.033231 test

1 Q0 G00-94-0326199 14 18.773146 test

1 Q0 G00-31-1216640 15 18.701529 test

1 Q0 G00-74-1802348 16 18.632754 test

1 Q0 G00-73-3632837 17 18.216664 test

1 Q0 G00-98-3517069 18 17.852850 test

1 Q0 G00-10-3730888 19 17.771361 test

1 Q0 G00-01-2689026 20 17.236037 test

1 Q0 G00-27-2669897 21 16.951894 test

1 Q0 G00-27-3209717 22 16.502528 test

1 Q0 G00-00-1006224 23 16.399435 test

1 Q0 G00-02-1239993 24 16.170523 test

1 Q0 G00-

In [173]:
# Iteration 1. Stemming- Finding Optimal Stemmer
# Put your code for creating the index here (you can add more cells).
LwrStpStmAnalyzer4 = RegexTokenizer() | LowercaseFilter() | StopFilter() | CustomFilter(WordNetLemmatizer().lemmatize)
# define a Schema with the new analyzer
SCHEMA_Q4_14 = Schema(file_path = ID(stored=True),
                   file_content = TEXT(analyzer = LwrStpStmAnalyzer4))

# create the index based on the new schema
INDEX_Q4_14 = createIndex(SCHEMA_Q4_14)
addFilesToIndex(INDEX_Q4_14, filesToIndex)

done indexing.


In [174]:
QP_Q4_14 = QueryParser("file_content", schema=INDEX_Q4_14.schema,group=qparser.OrGroup) # Replace None with your query parser for Q4_14
SEARCHER_Q4_14 = INDEX_Q4_14.searcher() # Replace None with your searcher for Q4_14

pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q4_14, SEARCHER_Q4_14)

1 mining gold silver coal
1 Q0 G00-07-1172041 0 23.797650 test

1 Q0 G00-86-3214229 1 23.280154 test

1 Q0 G00-90-0342721 2 22.803461 test

1 Q0 G00-21-2004003 3 22.618556 test

1 Q0 G00-42-1455285 4 21.533205 test

1 Q0 G00-27-2048511 5 20.408459 test

1 Q0 G00-23-3149835 6 20.098413 test

1 Q0 G00-34-1044519 7 19.285438 test

1 Q0 G00-32-2907392 8 19.215345 test

1 Q0 G00-50-2059900 9 19.213512 test

1 Q0 G00-94-0326199 10 19.157402 test

1 Q0 G00-26-0088644 11 19.129445 test

1 Q0 G00-24-4085400 12 19.045416 test

1 Q0 G00-02-0351712 13 18.981322 test

1 Q0 G00-74-1802348 14 18.455919 test

1 Q0 G00-31-1216640 15 18.303411 test

1 Q0 G00-10-3730888 16 17.118876 test

1 Q0 G00-01-2689026 17 17.027944 test

1 Q0 G00-98-3517069 18 16.816891 test

1 Q0 G00-48-3798484 19 16.727984 test

1 Q0 G00-62-3289850 20 16.165935 test

1 Q0 G00-27-2669897 21 15.978823 test

1 Q0 G00-91-0853670 22 15.407921 test

1 Q0 G00-08-0995170 23 15.251655 test

1 Q0 G00-73-3632837 24 15.135145 test

1 Q0 G00-

In [175]:
# Iteration 1. Stemming- Finding Optimal Stemmer
LwrStpStmAnalyzer5 = RegexTokenizer() | LowercaseFilter() | StopFilter() | StemFilter() | CustomFilter(LancasterStemmer().stem)
# define a Schema with the new analyzer
SCHEMA_Q4_15 = Schema(file_path = ID(stored=True),
                   file_content = TEXT(analyzer = LwrStpStmAnalyzer5))

# create the index based on the new schema
INDEX_Q4_15 = createIndex(SCHEMA_Q4_15)
addFilesToIndex(INDEX_Q4_15, filesToIndex)

done indexing.


In [176]:
QP_Q4_15 = QueryParser("file_content", schema=INDEX_Q4_15.schema,group=qparser.OrGroup) # Replace None with your query parser for Q4_15
SEARCHER_Q4_15 = INDEX_Q4_15.searcher() # Replace None with your searcher for Q4_15
pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q4_15, SEARCHER_Q4_15)

1 mining gold silver coal
1 Q0 G00-90-0342721 0 21.496289 test

1 Q0 G00-07-1172041 1 20.645999 test

1 Q0 G00-86-3214229 2 20.160815 test

1 Q0 G00-21-2004003 3 19.497800 test

1 Q0 G00-48-3798484 4 18.631231 test

1 Q0 G00-42-1455285 5 18.339958 test

1 Q0 G00-26-0088644 6 18.072792 test

1 Q0 G00-50-2059900 7 17.967568 test

1 Q0 G00-23-3149835 8 17.869745 test

1 Q0 G00-27-2048511 9 17.664293 test

1 Q0 G00-32-2907392 10 17.168617 test

1 Q0 G00-73-3632837 11 17.041948 test

1 Q0 G00-31-1216640 12 16.921988 test

1 Q0 G00-02-0351712 13 16.915273 test

1 Q0 G00-34-1044519 14 16.896144 test

1 Q0 G00-94-0326199 15 16.675084 test

1 Q0 G00-74-1802348 16 16.558017 test

1 Q0 G00-24-4085400 17 16.474789 test

1 Q0 G00-98-3517069 18 15.822402 test

1 Q0 G00-10-3730888 19 15.648412 test

1 Q0 G00-01-2689026 20 15.188399 test

1 Q0 G00-27-2669897 21 14.792254 test

1 Q0 G00-27-3209717 22 14.427091 test

1 Q0 G00-00-1006224 23 14.294081 test

1 Q0 G00-08-0995170 24 14.262627 test

1 Q0 G00-

In [177]:
# Iteration 2. Adding IntraWordFilter and Removing Numbers
# Put your code for creating the index here (you can add more cells).
LwrNumIntStpStmAnalyzer = RegexTokenizer() | LowercaseFilter() | SubstitutionFilter(r"\d+","") | IntraWordFilter() | StopFilter() | StemFilter() | CustomFilter(LancasterStemmer().stem)
# define a Schema with the new analyzer
SCHEMA_Q4_2 = Schema(file_path = ID(stored=True),
                   file_content = TEXT(analyzer = LwrNumIntStpStmAnalyzer))

# create the index based on the new schema
INDEX_Q4_2 = createIndex(SCHEMA_Q4_2)
addFilesToIndex(INDEX_Q4_2, filesToIndex)

done indexing.


In [178]:
QP_Q4_2 = QueryParser("file_content", schema=INDEX_Q4_3.schema,group=qparser.OrGroup) # Replace None with your query parser for Q4_3
SEARCHER_Q4_2 = INDEX_Q4_2.searcher() # Replace None with your searcher for Q4_3

pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q4_2, SEARCHER_Q4_2)

1 mining gold silver coal
1 Q0 G00-07-1172041 0 20.854511 test

1 Q0 G00-90-0342721 1 20.594114 test

1 Q0 G00-86-3214229 2 19.985034 test

1 Q0 G00-21-2004003 3 19.352118 test

1 Q0 G00-48-3798484 4 19.274966 test

1 Q0 G00-42-1455285 5 18.252889 test

1 Q0 G00-26-0088644 6 18.014430 test

1 Q0 G00-50-2059900 7 17.916552 test

1 Q0 G00-23-3149835 8 17.822690 test

1 Q0 G00-27-2048511 9 17.651733 test

1 Q0 G00-32-2907392 10 17.060655 test

1 Q0 G00-74-1802348 11 17.010934 test

1 Q0 G00-73-3632837 12 16.941885 test

1 Q0 G00-34-1044519 13 16.849524 test

1 Q0 G00-02-0351712 14 16.849406 test

1 Q0 G00-31-1216640 15 16.831408 test

1 Q0 G00-94-0326199 16 16.617504 test

1 Q0 G00-24-4085400 17 16.313829 test

1 Q0 G00-98-3517069 18 15.764016 test

1 Q0 G00-10-3730888 19 15.512143 test

1 Q0 G00-01-2689026 20 15.062816 test

1 Q0 G00-08-0995170 21 14.983204 test

1 Q0 G00-27-2669897 22 14.644994 test

1 Q0 G00-27-3209717 23 14.433994 test

1 Q0 G00-00-1006224 24 14.238263 test

1 Q0 G00-

In [0]:
# Iteration 3. Tuning the parameters (B,K1) of the BM25F Scoring algorithm to maximize MAP (Mean Average Precision)

# # Put your code for creating the index here (you can add more cells).
# LwrNumIntStpStmTunAnalyzer = RegexTokenizer() | LowercaseFilter() | SubstitutionFilter(r"\d+","") | IntraWordFilter() | StopFilter() | StemFilter() | CustomFilter(LancasterStemmer().stem)
# # define a Schema with the new analyzer
# SCHEMA_Q4_31 = Schema(file_path = ID(stored=True),
#                    file_content = TEXT(analyzer = LwrNumIntStpStmTunAnalyzer))

# # create the index based on the new schema
# INDEX_Q4_31 = createIndex(SCHEMA_Q4_31)
# addFilesToIndex(INDEX_Q4_31, filesToIndex)

In [0]:
# QP_Q4_31 = QueryParser("file_content", schema=INDEX_Q4_31.schema,group=qparser.OrGroup) # Replace None with your query parser for Q4_3
# B=[b for b in numpy.arange(0,1,0.02)]
# K1=[k1 for k1 in numpy.arange(0,5,0.1)]
# param_grid = {'B': B, 'K1' : K1}
# grid = ParameterGrid(param_grid)
# for params in grid:
#   w = scoring.BM25F(B=params['B'], content_B=1.0, K1=params['K1'])
#   SEARCHER_Q4_31 = INDEX_Q4_31.searcher(weighting=w)
#   print(params['B'],params['K1'])
#   pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q4_31, SEARCHER_Q4_31)

In [181]:
# Put your code for creating the index here (you can add more cells).
LwrNumIntStpStmTunAnalyzer = RegexTokenizer() | LowercaseFilter() | SubstitutionFilter(r"\d+","") | IntraWordFilter() | StopFilter() | StemFilter() | CustomFilter(LancasterStemmer().stem)
# define a Schema with the new analyzer
SCHEMA_Q4_3 = Schema(file_path = ID(stored=True),
                   file_content = TEXT(analyzer = LwrNumIntStpStmTunAnalyzer))

# create the index based on the new schema
INDEX_Q4_3 = createIndex(SCHEMA_Q4_3)
addFilesToIndex(INDEX_Q4_3, filesToIndex)

done indexing.


In [182]:
QP_Q4_3 = QueryParser("file_content", schema=INDEX_Q4_3.schema,group=qparser.OrGroup) # Replace None with your query parser for Q4_3
# SEARCHER_Q4_3 = INDEX_Q4_3.searcher() # Replace None with your searcher for Q4_3
w = scoring.BM25F(B=0.56, content_B=TEXT(analyzer=LwrNumIntStpStmAnalyzer), K1=4.7)
SEARCHER_Q4_3 = INDEX_Q4_3.searcher(weighting=w)
pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q4_3, SEARCHER_Q4_3)

1 mining gold silver coal
1 Q0 G00-23-3149835 0 38.997412 test

1 Q0 G00-27-2048511 1 38.901286 test

1 Q0 G00-42-1455285 2 37.378639 test

1 Q0 G00-74-1802348 3 35.922819 test

1 Q0 G00-02-0351712 4 35.452920 test

1 Q0 G00-32-2907392 5 34.854828 test

1 Q0 G00-48-3798484 6 33.218855 test

1 Q0 G00-86-3214229 7 33.125950 test

1 Q0 G00-90-0342721 8 32.806124 test

1 Q0 G00-73-3632837 9 32.784616 test

1 Q0 G00-26-0088644 10 32.372168 test

1 Q0 G00-07-1172041 11 32.320984 test

1 Q0 G00-50-2059900 12 31.816651 test

1 Q0 G00-34-1044519 13 31.794425 test

1 Q0 G00-94-0326199 14 31.719699 test

1 Q0 G00-31-1216640 15 31.083201 test

1 Q0 G00-10-3730888 16 27.610767 test

1 Q0 G00-24-4085400 17 27.319444 test

1 Q0 G00-21-2004003 18 26.360130 test

1 Q0 G00-85-1063363 19 25.610531 test

1 Q0 G00-98-3517069 20 25.578173 test

1 Q0 G00-27-2669897 21 25.065266 test

1 Q0 G00-62-3289850 22 24.832288 test

1 Q0 G00-10-3849661 23 23.049370 test

1 Q0 G00-01-2689026 24 23.030648 test

1 Q0 G00-

In [183]:
# Iteration 4. Increasing the corpus of stopwords rather than using the default ones in whoosh
nltk.download('stopwords')
stpwrds=list(set(stopwords.words('english')))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [184]:
# Put your code for creating the index here (you can add more cells).
LwrNumIntStpextStmTunAnalyzer = RegexTokenizer() | LowercaseFilter() | SubstitutionFilter(r"\d+","") | IntraWordFilter() | StopFilter(stoplist=stpwrds) | StemFilter() | CustomFilter(LancasterStemmer().stem)
# define a Schema with the new analyzer
SCHEMA_Q4 = Schema(file_path = ID(stored=True),
                   file_content = TEXT(analyzer = LwrNumIntStpextStmTunAnalyzer))

# create the index based on the new schema
INDEX_Q4 = createIndex(SCHEMA_Q4)
addFilesToIndex(INDEX_Q4, filesToIndex)

done indexing.


In [185]:
QP_Q4 = QueryParser("file_content", schema=INDEX_Q4.schema,group=qparser.OrGroup) # Replace None with your query parser for Q4
w = scoring.BM25F(B=0.56, content_B=1.0, K1=4.7)
SEARCHER_Q4 = INDEX_Q4.searcher(weighting=w) # Replace None with your searcher for Q4
pyTrecEval(TOPIC_FILE, QRELS_FILE, QP_Q4, SEARCHER_Q4)

1 mining gold silver coal
1 Q0 G00-23-3149835 0 39.210806 test

1 Q0 G00-27-2048511 1 38.233924 test

1 Q0 G00-42-1455285 2 37.684334 test

1 Q0 G00-02-0351712 3 35.476158 test

1 Q0 G00-74-1802348 4 35.347501 test

1 Q0 G00-32-2907392 5 35.115881 test

1 Q0 G00-73-3632837 6 33.030733 test

1 Q0 G00-86-3214229 7 32.677787 test

1 Q0 G00-48-3798484 8 32.532088 test

1 Q0 G00-26-0088644 9 32.431997 test

1 Q0 G00-07-1172041 10 31.943824 test

1 Q0 G00-90-0342721 11 31.911655 test

1 Q0 G00-50-2059900 12 31.857878 test

1 Q0 G00-34-1044519 13 31.832507 test

1 Q0 G00-94-0326199 14 31.766177 test

1 Q0 G00-31-1216640 15 31.462549 test

1 Q0 G00-10-3730888 16 27.453031 test

1 Q0 G00-24-4085400 17 26.879659 test

1 Q0 G00-21-2004003 18 26.010293 test

1 Q0 G00-85-1063363 19 25.529145 test

1 Q0 G00-98-3517069 20 25.263868 test

1 Q0 G00-27-2669897 21 24.919690 test

1 Q0 G00-62-3289850 22 24.418260 test

1 Q0 G00-10-3849661 23 22.952372 test

1 Q0 G00-01-2689026 24 22.923760 test

1 Q0 G00-

### Please answer the following questions here
**(a) A clear list of all final modifications made.**<br>
**Answer Q4 (a):**<br> 
Modifications made: (apart from those made in Q3)
1. Stemming- Finding Optimal Stemmer
2. Adding IntraWordFilter and Removing Numbers
3. Tuning the parameters (B,K1) of the BM25F Scoring algorithm to maximize MAP (Mean Average Precision)
4. Increasing the corpus of stopwords rather than using the default ones in whoosh

**(b)  Why each modification was made – how did it help?**<br>
**Answer Q4 (b):**<br>
With an objective of maximizing MAP i.e. retrieving highly ranked relevant documents following modifications were made: (apart from those made in Q3)
1. Stemming<br> 
<b>Motivation:</b> Words in different form can used in the same context. For instance, 'rendered', 'rendernesses', 'render', 'renderless', 'rendering' are the different forms of the root word 'render' with the same context. Thus, stemming the terms in queries and indexes can aid in finding better match of the document to the query and bringing relevant documents up the rank
<br>
<b>Benefits:</b> Stemming helps in finding the documents without worrying about word forms.
It reduces the size of the index, since it reduces the number of separate terms indexed by “collapsing” multiple word forms into a single base word.
[https://whoosh.readthedocs.io/en/latest/stemming.html]. The MAP improved from 0.3716 to 0.389 with the optimal stemming combination.

Iteration | Stemmer | MAP
--- | --- | ---
Q4_11 | StemFilter | 0.3709
Q4_12 | LancasterStemmer | 0.3795
Q4_13 | SnowballStemmer | 0.3697
Q4_14 | WordNetLemmatizer | 0.3744
Q4_15 | StemFilter+LancasterStemmer | 0.389

2. Adding IntraWordFilter and Removing Numbers<br>
<b>Motivation:</b>Words such as "TeleCommunication", "tele-communication" needs to be tokenized to "tele", "communications" which are relevant to topic ID 4- "whireless communications" to be able to matched with the relevant document.<br>
Also, on inspecting the index, it was obtained that there are terms in the field that are numberic. However, as per the information need, numberical characters are not required. Thus, SubstitutionFilter was used to detect numbers using regular expression. This will bring down the average field length and increasing the weightage of the rare terms in the document using in BM25 scoring algorithm.
<br>
<b>Benefits:</b> 
IntraWordFilter and SubstitutionFilter helps in reducing the size of the index and aid in finding better match of the document to the query and bringing relevant documents up the rank. The MAP improved from 0.389 to 0.3896
3. Tuning the parameters (B,K1) of the BM25F Scoring algorithm to maximize MAP (Mean Average Precision)<br>
<b>Motivation:</b> If a document is 300 pages long and mentions my name term once, it’s less likely to have as much to do with me as a short tweet which mentions me once.[https://www.elastic.co/blog/practical-bm25-part-2-the-bm25-algorithm-and-its-variables] The scale at which the length of the document affects the BM25f score is governed by the parameter 'B'. <br> Similarily, the parameter "K1" in the algorithm helps in controls the effect of the term frequency on the score i.e impact of tf on the score grows quickly when tf() ≤ k1 and slower and slower when tf() > k1. [https://www.elastic.co/blog/practical-bm25-part-2-the-bm25-algorithm-and-its-variables] Thus, there exists optimal combination of these parameters that can maximize the MAP. Accordingly, hyperparameters(B,K1) were tuned using grid search to optain optimal soultion.
<br>
<b>Benefits:</b>The optimal (B,K1) obtained was (0.56, 4.7). This improved the MAP from 0.3896 to 0.4031
 <br>
2. Increasing the corpus of stopwords rather than using the default ones in whoosh<br>
<b>Motivation:</b> Stopwords list pre-defined in the Whoosh StopFilter is not exhaustive to include all the standard corpus of stopwords. [https://github.com/jerem/Whoosh/blob/master/src/whoosh/analysis.py]. Thus, for further refinement, stopwords corpus from NLTK was used.
<br>
<b>Benefits:</b>Removing the stopwords not only helps in reducing the field length but also aids in giving more weight to the rare words in the query to match with the corresponding relevant documents. Thus the MAP improved from 0.4031 to 0.4116.
<br>

<b>The MAP Score with each modification is tabulated below:</b>

Iteration | Stemmer | MAP
--- | --- | ---
Q2 | Baseline | 0.1971
Q3 | LowerCase+StopFilter | 0.3716
Q4_11 | StemFilter | 0.3709
Q4_12 | LancasterStemmer | 0.3795
Q4_13 | SnowballStemmer | 0.3697
Q4_14 | WordNetLemmatizer | 0.3744
Q4_15 | StemFilter+LancasterStemmer | 0.389
Q4_2 | SubstitutionFilter+IntraWordFilter | 0.3896
Q4_3 | BM25F Hyperparamater Tuning | 0.4031
Q4 | NLTK Stopwords corpus | 0.4116

**(c)**  **The  final  MAP  performance  that  these  modifications  attained.**<br>
**Answer Q4 (c):**<br>
0.4116

In [0]:
# INDEX_Q4 = None # Replace None with your index for Q4
# QP_Q4 = None # Replace None with your query parser for Q4
# SEARCHER_Q4 = None # Replace None with your searcher for Q4

## Validation

In [0]:
# Run the following cells to make sure your code returns the correct value types

In [0]:
from whoosh.index import FileIndex
from whoosh.qparser import QueryParser
from whoosh.searching import Searcher
import os.path

### Q2 Validation

In [189]:
assert(isinstance(INDEX_Q2, FileIndex)), "Index Type"
assert(isinstance(QP_Q2, QueryParser)), "Query Parser Type"
assert(isinstance(SEARCHER_Q2, Searcher)), "Searcher Type"
print("Q2 Types Validated")

Q2 Types Validated


### Q3 Validation

In [190]:
assert(isinstance(INDEX_Q3, FileIndex)), "Index Type"
assert(isinstance(QP_Q3, QueryParser)), "Query Parser Type"
assert(isinstance(SEARCHER_Q3, Searcher)), "Searcher Type"
print("Q3 Types Validated")

Q3 Types Validated


### Q4 Validation (Graduate Students)

In [191]:
assert(isinstance(INDEX_Q4, FileIndex)), "Index Type"
assert(isinstance(QP_Q4, QueryParser)), "Query Parser Type"
assert(isinstance(SEARCHER_Q4, Searcher)), "Searcher Type"
print("Q4 Types Validated")

Q4 Types Validated
